In [ ]:
import torch

In [ ]:
class MyModelLN(torch.nn.Module):
    class Block(torch.nn.Module):
        def __init__(self, in_channels, out_channels):
            super().__init__()
            self.model = torch.nn.Sequential(
                torch.nn.Linear(in_channels, out_channels),
                torch.nn.LayerNorm(out_channels),
                torch.nn.ReLU(),
                torch.nn.Linear(out_channels, out_channels),
                torch.nn.LayerNorm(out_channels),
                torch.nn.ReLU(),
            )
            if in_channels != out_channels:
                self.skip = torch.nn.Linear(in_channels, out_channels)
            else:
                self.skip = torch.nn.Identity()

        def forward(self, x):
            return self.skip(x) + self.model(x)

    def __init__(self, layer_size=[512, 512, 512]):
        super().__init__()
        layers = []
        layers.append(torch.nn.Flatten())
        c = 128 * 128 * 3
        layers.append(torch.nn.Linear(c, 512, bias=False))
        c = 512
        for s in layer_size:
            layers.append(self.Block(c, s))
            c = s
        layers.append(torch.nn.Linear(c, 102, bias=False))
        self.model = torch.nn.Sequential(*layers)

    def forward(self, x):
        return self.model(x)


x = torch.randn(10, 3, 128, 128)
net = MyModelLN([512] * 4)
print(net(x))

In [ ]:
128 * 128 * 3